In [ ]:
import sys

import ipyparallel as ipp
import os, time
import numpy as np
import scipy as sp
import numbers
from sklearn import preprocessing
from subprocess import Popen, PIPE
import seaborn as sns
from IPython.display import FileLink
import urllib.request as urllib2
import dill
import traceback
from pandas import Series, DataFrame
import gzip
import warnings
warnings.filterwarnings('ignore',category=pd.io.pytables.PerformanceWarning)
%config InlineBackend.figure_format = 'retina'
from Bio import SeqIO
import pysam
from collections import OrderedDict, namedtuple
import operator
import multiprocessing as mp

In [ ]:
vcfutils = "perl /home/menonm2/g/src/bcftools-1.3/vcfutils.pl"
vcftools = "/home/menonm2/g/bin/vcftools"
bcftools = "/home/menonm2/g/src/bcftools-1.3.1/bcftools"
tabix = "/home/menonm2/g/src/dDocent_run/freebayes/SeqLib/htslib/tabix"
bgzip = "/home/menonm2/g/src/dDocent_run/freebayes/SeqLib/htslib/bgzip"
java  = "/home/menonm2/jdk1.8.0_91/bin/java"
plink = "/home/menonm2/g/src/plink-1.07-x86_64/plink --noweb"

Load in the output file generated from dDocent run. 

In [ ]:
analysis_dir = '/home/menonm2/eckertlab/Mitra/chapter2/dDocent3489_SNPs_JCB'

vcf_file = os.path.join(analysis_dir, "TotalRawSNPs.vcf")
assert os.path.exists(vcf_file)
vcf_file

In [ ]:
!$vcftools --remove-indels \
--max-missing 0.5 \
--min-alleles 2 \
--max-alleles 2 \
--remove-filtered-all \
--recode \
--recode-INFO-all \
--gzvcf \
$vcf_file \
--out $vcf_file

Just renaming files 

In [ ]:
vcf_filtered = "%s.recode.vcf" % vcf_file
vcf_filtered_gz = "%s.gz" % vcf_filtered

In [ ]:
!$bgzip -c $vcf_filtered > {vcf_filtered_gz}
!$tabix {vcf_filtered_gz}

Functions to obtain several summary stats to perform further custom filtering on the vcf file

In [ ]:
def get_vcf_stats(vcf_gz):
    
    stats = ['depth',
            'site-depth',
            'site-mean-depth',
            'site-quality',
            'missing-indv',
            'missing-site',
            'freq',
            'counts',
            'hardy',
            'het']
    
    for stat in stats:
        !$vcftools --gzvcf $vcf_gz \
        --out $vcf_gz \
        {"--%s" % stat} 

In [ ]:
pd.set_option('display.max_columns', 100)

def get_MAF(row):
    try:
        return np.min([row.A1_freq, row.A2_freq])
    except:
        print(row)
        
def get_correction(n):
    #for finite sample size
    return (2*n)/(2*n-1)

def calculate_Fis(vals):
    try:
        data = [float(x) for x in vals.split("/")]
        assert len(data) == 3
        num_individuals = np.sum(data)
        total_alleles = 2*num_individuals
        a1_count = 2*data[0]
        a2_count = 2*data[2]
        het_count = data[1]
        a1_count += het_count
        a2_count += het_count
        a1_freq = a1_count/total_alleles
        a2_freq = a2_count/total_alleles
        assert a1_freq + a2_freq == 1.0
        He = 2 * a1_freq * a2_freq * get_correction(num_individuals)
        Ho = het_count/num_individuals
        Fis = 1 - (Ho/He)
        return Fis
    except:
        return -9

def combine_vcf_stats(filedir, prefix):
    hardy_files = !ls {filedir}/{prefix}*.hwe
    hardy = pd.read_csv(hardy_files[0], sep="\t")

    hardy.columns = ['CHROM', 'POS', 'OBS(HOM1/HET/HOM2)', 'E(HOM1/HET/HOM2)', 'ChiSq_HWE',
       'P_HWE', 'P_HET_DEFICIT', 'P_HET_EXCESS']
    hardy.index = hardy.apply(lambda x: "%s-%d" % (x.CHROM, x.POS), axis=1)
    
    loci_files = !ls {filedir}/{prefix}*.l* | grep -v log
    loci_df = pd.concat([pd.read_csv(x, sep="\t", skiprows=0) for x in loci_files], axis=1)
    chrom_pos = loci_df.ix[:,0:2]
    
    frq_files = !ls {filedir}/{prefix}*.frq* | grep -v count
    frq_data = []
    h = open(frq_files[0])
    header = h.readline().strip().split()
    for line in h:
        frq_data.append(line.strip().split('\t'))

    header = ['CHROM', 'POS', 'N_ALLELES', 'N_CHR', 'A1_FREQ', "A2_FREQ"]
    frq_df = pd.DataFrame(frq_data)
    print(frq_df.columns)
    #frq_df = frq_df.drop([6,7],axis=1)
    frq_df.columns = header
    frq_df.index = frq_df.apply(lambda x: "%s-%s" % (x.CHROM, x.POS), axis=1)
    
    loci_df = loci_df.drop(['CHROM','CHR','POS'], axis=1)
    loci_df = pd.concat([chrom_pos, loci_df], axis=1)
    loci_df.index = loci_df.apply(lambda x: "%s-%d" % (x.CHROM, x.POS), axis=1)
    
    loci_df = pd.concat([loci_df, frq_df, hardy], axis=1)
    loci_df["A1_allele"] = loci_df.apply(lambda row: row.A1_FREQ.split(":")[0], axis=1)
    loci_df["A2_allele"] = loci_df.apply(lambda row: row.A2_FREQ.split(":")[0], axis=1)
    
    loci_df["A1_freq"] = loci_df.apply(lambda row: float(row.A1_FREQ.split(":")[1]), axis=1)
    loci_df["A2_freq"] = loci_df.apply(lambda row: float(row.A2_FREQ.split(":")[1]), axis=1)
    
    loci_df['MAF'] = loci_df.apply(get_MAF, axis=1)
    loci_df = loci_df.drop(['CHROM', 'POS'], axis=1)
    
    loci_df['Fis'] = loci_df['OBS(HOM1/HET/HOM2)'].apply(calculate_Fis)
    
    return loci_df, frq_df, hardy

In [ ]:
get_vcf_stats(vcf_filtered_gz)

In [ ]:
loci_df, frq_df, hardy = combine_vcf_stats(analysis_dir, "TotalRawSNPs.vcf.recode.vcf") 

In [ ]:
loci_df.shape

In [ ]:
loci_df.to_csv(os.path.join(analysis_dir, "loci_stats_raw.txt"),
              sep="\t",
              index=False)

I need to generate a map of all the position information stored in the vcf file to be able use plink. I am using plink to get a 012 file.

In [ ]:
chroms = sorted(set([x.split("-")[0] for x in loci_df.index]))

In [ ]:
with open(os.path.join(analysis_dir, "chrom_map_raw.txt"), "w") as o:
    for i, c in enumerate(chroms):
        o.write("%s\t%d\n" % (c, i))

In [ ]:
def write_plink_files(vcf_gz):
    !$vcftools --gzvcf {vcf_gz} \
    --out {vcf_gz} \
    --plink \
    --chrom-map {os.path.join(analysis_dir, "chrom_map_raw.txt")}

In [ ]:
write_plink_files(vcf_filtered_gz)

In [ ]:
def write_plink_recode(vcf_gz):
    !$plink --recodeA --tab --file {vcf_gz} --out {vcf_gz}_recodeA
    

In [ ]:
write_plink_recode(vcf_filtered_gz)

Now, we will use the outputs from the custom functions above to filter SNPs. 
First look at depth distribution across SNPs to filter based on depth. 

In [ ]:
loci_df.SUM_DEPTH.describe() 

Look at distribution of Fis values, phred score and MAF across SNPs.

In [ ]:
len(loci_df[loci_df.Fis == -9])

In [ ]:
len(loci_df[loci_df.QUAL >= 10]) - len(loci_df[loci_df.QUAL >= 20])

In [ ]:
len(loci_df[loci_df.QUAL < 20]), len(loci_df[loci_df.QUAL < 10])

In [ ]:
len(loci_df[loci_df.Fis >= 0.5]), len(loci_df[loci_df.Fis <= -0.5]), len(loci_df[loci_df.MAF < 0.002])

Perform the filtering based on these stats

In [ ]:
##MAF should be set lower than the pop with smallest no of indvs
#changed depth to match the values in loci_df.SUM_DEPTH min and 75th percentile or 50th percentile
def filter_snps(df):
        return df[(df.SUM_DEPTH >= 600) & 
                  (df.SUM_DEPTH < 3931) & 
                  (df.QUAL >= 20) & 
                  (df.MAF >= 0.001) & 
                  (df.Fis < 0.5) & 
                  (df.Fis > -0.5)]

In [ ]:
loci_stage1 = filter_snps(loci_df)
loci_stage1.shape

In [ ]:
with open(os.path.join(analysis_dir, "75perc_positions.txt"), "w") as o:
    for elem in loci_stage.index:
        o.write("%s\n" % "\t".join(elem.split("-")))

In [ ]:
for d, vcf_gz in zip([analysis_dir], [vcf_filtered_gz]):
    !$vcftools --gzvcf $vcf_gz \
    --remove-indels  \
    --remove-filtered-all \
    --recode \
    --recode-INFO-all \
    --positions {os.path.join(d, "Raw75perc_positions.txt")} \
    --out {os.path.join(d, "Rawgood_snps75perc")}

In [ ]:
for d in [analysis_dir]:
    snps = os.path.join(d, "good_snps75perc.recode.vcf")
    snps_gz = snps + ".gz"
    !$bgzip -c {snps} > {snps_gz}
    !$tabix {snps_gz}
    
    srted = snps_gz + "_sorted.vcf"
    srted_gz = srted + ".gz"
    !vcf-sort {snps_gz} > {srted}
    !$bgzip -c {srted} > {srted_gz}
    !$tabix {srted_gz}

In [ ]:
for d in [analysis_dir]:
    f = os.path.join(d, "good_snps75perc.recode.vcf.gz_sorted.vcf.gz")
    assert os.path.exists(f)
    write_plink_recode(f) #will return the final file in 012 format 